In [1]:
from data201 import db_connection, df_query

In [2]:
conn = db_connection('ZAGI-Sales.ini')

## Which products sell below the average price?
### What is the average price?

In [3]:
df = df_query(conn, 
    """
    SELECT AVG(product_price)
    FROM   product
    """
)

display(df)

AVG(product_price)
0               112.5

### Products selling below the average price.

In [4]:
df = df_query(conn, 
    """
    SELECT product_id, product_name, product_price
    FROM   product
    WHERE  product_price < (
        SELECT AVG(product_price)
        FROM   product
    )
    """
)

display(df)

product_id product_name  product_price
0        1X1      Zzz Bag          100.0
1        2X2    Easy Boot           70.0
2        3X3    Cosy Sock           15.0
3        4X4    Dura Boot           90.0

## What is the name, id, and price of products that have more than 3 items sold in all sales transactions?
### Number of product items sold.

In [5]:
df = df_query(conn, 
    """
    SELECT product_id, no_of_items
    FROM sold_via
    """
)

display(df)

product_id  no_of_items
0        1X1            1
1        1X1            1
2        1X1            2
3        2X2            1
4        2X2            2
5        3X3            5
6        4X4            1
7        4X4            4
8        5X5            2
9        6X6            1

### Products that sold more than 3 items.

In [6]:
df = df_query(conn, 
    """
    SELECT product_id, SUM(no_of_items)
    FROM sold_via
    GROUP BY product_id
    HAVING SUM(no_of_items) > 3
    """
)

display(df)

product_id  SUM(no_of_items)
0        1X1               4.0
1        3X3               5.0
2        4X4               5.0

### Product id, name, and price.

In [7]:
df = df_query(conn, 
    """
    SELECT product_id, product_name, product_price
    FROM product
    WHERE product_id IN (
        SELECT product_id
        FROM sold_via
        GROUP BY product_id
        HAVING SUM(no_of_items) > 3
    )
    """
)

display(df)

product_id product_name  product_price
0        1X1      Zzz Bag          100.0
1        3X3    Cosy Sock           15.0
2        4X4    Dura Boot           90.0

# What is the name, id, and price of products that were each sold in more than one sales transaction?
### Sales transactions.

In [8]:
df = df_query(conn, 
    """
    SELECT product_id, tid
    FROM sold_via
    """
)

display(df)

product_id   tid
0        1X1  T111
1        2X2  T222
2        1X1  T333
3        3X3  T333
4        2X2  T444
5        4X4  T444
6        4X4  T555
7        5X5  T555
8        6X6  T555
9        1X1  T666

### More than one transaction.

In [9]:
df = df_query(conn, 
    """
    SELECT product_id
    FROM sold_via
    GROUP BY product_id
    HAVING COUNT(*) > 1
    """
)

display(df)

product_id
0        1X1
1        2X2
2        4X4

### Product id, name, and price.

In [10]:
df = df_query(conn, 
    """
    SELECT product_id, product_name, product_price
    FROM product
    WHERE product_id IN (
         SELECT product_id
         FROM sold_via
         GROUP BY product_id
         HAVING COUNT(*) > 1
    )
    """
)

display(df)

product_id product_name  product_price
0        1X1      Zzz Bag          100.0
1        2X2    Easy Boot           70.0
2        4X4    Dura Boot           90.0

In [11]:
conn.close()